In [ ]:
import pandas as pd
import numpy as np
from analytics.basket_index import MarkitBasketIndex
import matplotlib.pyplot as plt

from db import dbengine
from ipywidgets import widgets
engine = dbengine('serenitasdb')

In [ ]:
w = widgets.Dropdown(
    options=['IG', 'HY', 'EU'],
    value='IG',
    description='Index:',
    disabled=False,
)
w

In [ ]:
w_1 = widgets.IntSlider(value=30, min=22, max=30, description = 'Series')
w_1

In [ ]:
trade_date = (pd.datetime.today() - pd.offsets.BDay(1)).date()
index_type = w.value
series = w_1.value

In [ ]:
sql_string = "select * from index_members(%s, %s)"
df = pd.read_sql_query(sql_string, engine, params=(index_type + str(series), trade_date), index_col=['markit_ticker'])
df1 = pd.read_sql_query(sql_string, engine, params=(index_type + str(series-1), trade_date), index_col=['markit_ticker'])

In [ ]:
#Removals
df1.loc[df1.index.difference(df.index)]

In [ ]:
#Additions
df.loc[df.index.difference(df1.index)]

In [ ]:
date_range = pd.bdate_range(trade_date - 52 * pd.offsets.Week(), trade_date, freq='5B')
index = MarkitBasketIndex(index_type, series, ['5yr'])
default_prob = {}
maturity = np.array([np.datetime64(index.maturities[0]).view('int') + 134774])
for d in date_range:
    index.value_date = d
    surv_prob, tickers = index.survival_matrix(maturity)
    default_prob[d] = pd.Series(1 - np.ravel(surv_prob), index=tickers)
default_prob = pd.concat(default_prob)

In [ ]:
#Top 20 highest cumulative
top20 = default_prob.unstack(-1)[default_prob[trade_date].nlargest(20).index]
top20.index.name='date'
top20.columns.name='tickers'
top20.plot(title=f'market implied default probabilities to {index.maturities[0]}')

In [ ]:
title = 'market implied default probabilities to ' + str(temp.maturities[0])
fig, ax = plt.subplots()
ax.plot(dp_top.T)
ax.set(xlabel='date', ylabel='probability',
       title=title)
ax.legend(dp_top.index, loc='upper center', bbox_to_anchor=(1.3, 1), ncol=1)
fig.set_size_inches(10, 6)
fig.tight_layout()